# Imports

In [1]:
import os
import gc
import pickle

In [2]:
from flair.data import Sentence
from flair.models import SequenceTagger
from flair.models import TextClassifier

from flair.data import TaggedCorpus
from flair.data_fetcher import  NLPTaskDataFetcher, NLPTask

Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex.


In [3]:
import torch

# Initialize Mongo database

In [4]:
from pymongo import MongoClient

client = MongoClient()

db = client['glvis_db']

# Extract hidden representations from flair's pretrained Chunking model

In [ ]:
db_col = db['flair_chunk']

In [ ]:
chunk_tagger = SequenceTagger.load('chunk')

In [ ]:
corpus: TaggedCorpus = NLPTaskDataFetcher.load_corpus(NLPTask.CONLL_2000)

In [ ]:
tag_type = 'np'
tag_dictionary = corpus.make_tag_dictionary(tag_type=tag_type)

In [ ]:
for i, sentence in enumerate(corpus.get_all_sentences()):
    print(f'Start sentence {i}')
    
    # Define hook to get intermediate values
    hidden_states = torch.zeros(len(sentence), 1, 512)
    def hook(m, i):
        hidden_states.copy_(i[0].data)
                                
    h = pos_tagger.linear.register_forward_pre_hook(hook)
                                
    pos_tagger.predict(sentence)
                                
    spans = sentence.get_spans('chunk')
                                
    # Informaction to store: the named entities, their predicted labels, probabilities and hidden states
    # If there are multiple words for one entity, take the average value of hidden states
    # and record the number of words in the entity
    
    for span in spans:
        entry = {}
        entry['text'] = span.text
        entry['tag'] = span.tag
        entry['score'] = span.score
        entry['token_num'] = len(span.tokens)
        
        idx = [token.idx-1 for token in span.tokens]
        entry['linear_layer_state'] = hidden_states[idx, :, :].mean(dim=0).squeeze().tolist()
        
        db_col.insert_one(entry)
    
    h.remove()
    
    print(f'Finish sentence {i}')

# Extract hidden representations from flair's pretrained POS model

In [15]:
db_col = db['flair_pos']

In [5]:
pos_tagger = SequenceTagger.load('pos')

2019-03-20 11:12:13,463 loading file /home/snie/.flair/models/en-pos-ontonotes-v0.2.pt


In [6]:
base_path='/home/snie/Workspace/glvis/models/data/conll/OntoNotes-5.0-NER-BIO/'

In [7]:
corpus: TaggedCorpus = NLPTaskDataFetcher.load_corpus(NLPTask.ONTONER, base_path=base_path)

2019-03-20 11:12:34,723 Reading data from /home/snie/Workspace/glvis/models/data/conll/OntoNotes-5.0-NER-BIO/ontoner
2019-03-20 11:12:34,723 Train: /home/snie/Workspace/glvis/models/data/conll/OntoNotes-5.0-NER-BIO/ontoner/onto.train.ner
2019-03-20 11:12:34,724 Dev: /home/snie/Workspace/glvis/models/data/conll/OntoNotes-5.0-NER-BIO/ontoner/onto.development.ner
2019-03-20 11:12:34,724 Test: /home/snie/Workspace/glvis/models/data/conll/OntoNotes-5.0-NER-BIO/ontoner/onto.test.ner


In [8]:
tag_dictionary = corpus.make_tag_dictionary(tag_type='pos')

In [29]:
db_col.drop()

In [ ]:
for i, sentence in enumerate(corpus.get_all_sentences()):
    print(f'Start sentence {i}')
    
    # Define hook to get intermediate values
    hidden_states = torch.zeros(len(sentence), 1, 512)
    def hook(m, i):
        hidden_states.copy_(i[0].data)
                                
    h = pos_tagger.linear.register_forward_pre_hook(hook)
                                
    pos_tagger.predict(sentence)
                                
    spans = sentence.get_spans('pos')
                                
    # Informaction to store: the named entities, their predicted labels, probabilities and hidden states
    # If there are multiple words for one entity, take the average value of hidden states
    # and record the number of words in the entity
    
    for span in spans:
        entry = {}
        entry['text'] = span.text
        entry['tag'] = span.tag
        entry['score'] = span.score
        entry['token_num'] = len(span.tokens)
        
        idx = span.tokens[0].idx - 1
        entry['linear_layer_state'] = hidden_states[idx, :, :].squeeze().tolist()
        
        db_col.insert_one(entry)
    
    h.remove()
    
    print(f'Finish sentence {i}')

Start sentence 0
Finish sentence 0
Start sentence 1
Finish sentence 1
Start sentence 2
Finish sentence 2
Start sentence 3
Finish sentence 3
Start sentence 4
Finish sentence 4
Start sentence 5
Finish sentence 5
Start sentence 6
Finish sentence 6
Start sentence 7
Finish sentence 7
Start sentence 8
Finish sentence 8
Start sentence 9
Finish sentence 9
Start sentence 10
Finish sentence 10
Start sentence 11
Finish sentence 11
Start sentence 12
Finish sentence 12
Start sentence 13
Finish sentence 13
Start sentence 14
Finish sentence 14
Start sentence 15
Finish sentence 15
Start sentence 16
Finish sentence 16
Start sentence 17
Finish sentence 17
Start sentence 18
Finish sentence 18
Start sentence 19
Finish sentence 19
Start sentence 20
Finish sentence 20
Start sentence 21
Finish sentence 21
Start sentence 22
Finish sentence 22
Start sentence 23
Finish sentence 23
Start sentence 24
Finish sentence 24
Start sentence 25
Finish sentence 25
Start sentence 26
Finish sentence 26
Start sentence 27
Fin

Finish sentence 216
Start sentence 217
Finish sentence 217
Start sentence 218
Finish sentence 218
Start sentence 219
Finish sentence 219
Start sentence 220
Finish sentence 220
Start sentence 221
Finish sentence 221
Start sentence 222
Finish sentence 222
Start sentence 223
Finish sentence 223
Start sentence 224
Finish sentence 224
Start sentence 225
Finish sentence 225
Start sentence 226
Finish sentence 226
Start sentence 227
Finish sentence 227
Start sentence 228
Finish sentence 228
Start sentence 229
Finish sentence 229
Start sentence 230
Finish sentence 230
Start sentence 231
Finish sentence 231
Start sentence 232
Finish sentence 232
Start sentence 233
Finish sentence 233
Start sentence 234
Finish sentence 234
Start sentence 235
Finish sentence 235
Start sentence 236
Finish sentence 236
Start sentence 237
Finish sentence 237
Start sentence 238
Finish sentence 238
Start sentence 239
Finish sentence 239
Start sentence 240
Finish sentence 240
Start sentence 241
Finish sentence 241
Start

Finish sentence 427
Start sentence 428
Finish sentence 428
Start sentence 429
Finish sentence 429
Start sentence 430
Finish sentence 430
Start sentence 431
Finish sentence 431
Start sentence 432
Finish sentence 432
Start sentence 433
Finish sentence 433
Start sentence 434
Finish sentence 434
Start sentence 435
Finish sentence 435
Start sentence 436
Finish sentence 436
Start sentence 437
Finish sentence 437
Start sentence 438
Finish sentence 438
Start sentence 439
Finish sentence 439
Start sentence 440
Finish sentence 440
Start sentence 441
Finish sentence 441
Start sentence 442
Finish sentence 442
Start sentence 443
Finish sentence 443
Start sentence 444
Finish sentence 444
Start sentence 445
Finish sentence 445
Start sentence 446
Finish sentence 446
Start sentence 447
Finish sentence 447
Start sentence 448
Finish sentence 448
Start sentence 449
Finish sentence 449
Start sentence 450
Finish sentence 450
Start sentence 451
Finish sentence 451
Start sentence 452
Finish sentence 452
Start

Finish sentence 641
Start sentence 642
Finish sentence 642
Start sentence 643
Finish sentence 643
Start sentence 644
Finish sentence 644
Start sentence 645
Finish sentence 645
Start sentence 646
Finish sentence 646
Start sentence 647
Finish sentence 647
Start sentence 648
Finish sentence 648
Start sentence 649
Finish sentence 649
Start sentence 650
Finish sentence 650
Start sentence 651
Finish sentence 651
Start sentence 652
Finish sentence 652
Start sentence 653
Finish sentence 653
Start sentence 654
Finish sentence 654
Start sentence 655
Finish sentence 655
Start sentence 656
Finish sentence 656
Start sentence 657
Finish sentence 657
Start sentence 658
Finish sentence 658
Start sentence 659
Finish sentence 659
Start sentence 660
Finish sentence 660
Start sentence 661
Finish sentence 661
Start sentence 662
Finish sentence 662
Start sentence 663
Finish sentence 663
Start sentence 664
Finish sentence 664
Start sentence 665
Finish sentence 665
Start sentence 666
Finish sentence 666
Start

Finish sentence 852
Start sentence 853
Finish sentence 853
Start sentence 854
Finish sentence 854
Start sentence 855
Finish sentence 855
Start sentence 856
Finish sentence 856
Start sentence 857
Finish sentence 857
Start sentence 858
Finish sentence 858
Start sentence 859
Finish sentence 859
Start sentence 860
Finish sentence 860
Start sentence 861
Finish sentence 861
Start sentence 862
Finish sentence 862
Start sentence 863
Finish sentence 863
Start sentence 864
Finish sentence 864
Start sentence 865
Finish sentence 865
Start sentence 866
Finish sentence 866
Start sentence 867
Finish sentence 867
Start sentence 868
Finish sentence 868
Start sentence 869
Finish sentence 869
Start sentence 870
Finish sentence 870
Start sentence 871
Finish sentence 871
Start sentence 872
Finish sentence 872
Start sentence 873
Finish sentence 873
Start sentence 874
Finish sentence 874
Start sentence 875
Finish sentence 875
Start sentence 876
Finish sentence 876
Start sentence 877
Finish sentence 877
Start

...

Finish sentence 64930
Start sentence 64931
Finish sentence 64931
Start sentence 64932
Finish sentence 64932
Start sentence 64933
Finish sentence 64933
Start sentence 64934
Finish sentence 64934
Start sentence 64935
Finish sentence 64935
Start sentence 64936
Finish sentence 64936
Start sentence 64937
Finish sentence 64937
Start sentence 64938
Finish sentence 64938
Start sentence 64939
Finish sentence 64939
Start sentence 64940
Finish sentence 64940
Start sentence 64941
Finish sentence 64941
Start sentence 64942
Finish sentence 64942
Start sentence 64943
Finish sentence 64943
Start sentence 64944
Finish sentence 64944
Start sentence 64945
Finish sentence 64945
Start sentence 64946
Finish sentence 64946
Start sentence 64947
Finish sentence 64947
Start sentence 64948
Finish sentence 64948
Start sentence 64949
Finish sentence 64949
Start sentence 64950
Finish sentence 64950
Start sentence 64951
Finish sentence 64951
Start sentence 64952
Finish sentence 64952
Start sentence 64953
Finish sent

Finish sentence 65122
Start sentence 65123
Finish sentence 65123
Start sentence 65124
Finish sentence 65124
Start sentence 65125
Finish sentence 65125
Start sentence 65126
Finish sentence 65126
Start sentence 65127
Finish sentence 65127
Start sentence 65128
Finish sentence 65128
Start sentence 65129
Finish sentence 65129
Start sentence 65130
Finish sentence 65130
Start sentence 65131
Finish sentence 65131
Start sentence 65132
Finish sentence 65132
Start sentence 65133
Finish sentence 65133
Start sentence 65134
Finish sentence 65134
Start sentence 65135
Finish sentence 65135
Start sentence 65136
Finish sentence 65136
Start sentence 65137
Finish sentence 65137
Start sentence 65138
Finish sentence 65138
Start sentence 65139
Finish sentence 65139
Start sentence 65140
Finish sentence 65140
Start sentence 65141
Finish sentence 65141
Start sentence 65142
Finish sentence 65142
Start sentence 65143
Finish sentence 65143
Start sentence 65144
Finish sentence 65144
Start sentence 65145
Finish sent

Finish sentence 65315
Start sentence 65316
Finish sentence 65316
Start sentence 65317
Finish sentence 65317
Start sentence 65318
Finish sentence 65318
Start sentence 65319
Finish sentence 65319
Start sentence 65320
Finish sentence 65320
Start sentence 65321
Finish sentence 65321
Start sentence 65322
Finish sentence 65322
Start sentence 65323
Finish sentence 65323
Start sentence 65324
Finish sentence 65324
Start sentence 65325
Finish sentence 65325
Start sentence 65326
Finish sentence 65326
Start sentence 65327
Finish sentence 65327
Start sentence 65328
Finish sentence 65328
Start sentence 65329
Finish sentence 65329
Start sentence 65330
Finish sentence 65330
Start sentence 65331
Finish sentence 65331
Start sentence 65332
Finish sentence 65332
Start sentence 65333
Finish sentence 65333
Start sentence 65334
Finish sentence 65334
Start sentence 65335
Finish sentence 65335
Start sentence 65336
Finish sentence 65336
Start sentence 65337
Finish sentence 65337
Start sentence 65338
Finish sent

Finish sentence 65509
Start sentence 65510
Finish sentence 65510
Start sentence 65511
Finish sentence 65511
Start sentence 65512
Finish sentence 65512
Start sentence 65513
Finish sentence 65513
Start sentence 65514
Finish sentence 65514
Start sentence 65515
Finish sentence 65515
Start sentence 65516
Finish sentence 65516
Start sentence 65517
Finish sentence 65517
Start sentence 65518
Finish sentence 65518
Start sentence 65519
Finish sentence 65519
Start sentence 65520
Finish sentence 65520
Start sentence 65521
Finish sentence 65521
Start sentence 65522
Finish sentence 65522
Start sentence 65523
Finish sentence 65523
Start sentence 65524
Finish sentence 65524
Start sentence 65525
Finish sentence 65525
Start sentence 65526
Finish sentence 65526
Start sentence 65527
Finish sentence 65527
Start sentence 65528
Finish sentence 65528
Start sentence 65529
Finish sentence 65529
Start sentence 65530
Finish sentence 65530
Start sentence 65531
Finish sentence 65531
Start sentence 65532
Finish sent

Finish sentence 65702
Start sentence 65703
Finish sentence 65703
Start sentence 65704
Finish sentence 65704
Start sentence 65705
Finish sentence 65705
Start sentence 65706


# Extract hidden representations from flair's pretrained NER model

In [ ]:
db_col = db['flair_ner']

In [4]:
ner = SequenceTagger.load('ner')

2019-03-19 14:12:05,408 loading file /home/snie/.flair/models/en-ner-conll03-v0.4.pt


In [5]:
corpus = NLPTaskDataFetcher.load_corpus(NLPTask.CONLL_03, base_path='data/conll/')

2019-03-19 14:12:09,359 Reading data from data/conll/conll_03
2019-03-19 14:12:09,360 Train: data/conll/conll_03/eng.train
2019-03-19 14:12:09,360 Dev: data/conll/conll_03/eng.testa
2019-03-19 14:12:09,360 Test: data/conll/conll_03/eng.testb


In [6]:
tag_dictionary = corpus.make_tag_dictionary(tag_type='ner')

In [13]:
tag_set = set()
counter = 0
for entry in db['flair_ner'].find():
    counter += 1
    tag_set.add(entry['tag'])

In [12]:
tag_set

{'LOC', 'MISC', 'ORG', 'PER'}

In [9]:
tag_dictionary.get_items()

['<unk>',
 'O',
 'S-ORG',
 'S-MISC',
 'B-PER',
 'E-PER',
 'S-LOC',
 'B-ORG',
 'E-ORG',
 'I-PER',
 'S-PER',
 'B-MISC',
 'I-MISC',
 'E-MISC',
 'I-ORG',
 'B-LOC',
 'E-LOC',
 'I-LOC',
 '<START>',
 '<STOP>']

In [7]:
len(corpus.get_all_sentences())

22137

In [8]:
db_col.drop()

In [ ]:
for i, sentence in enumerate(corpus.get_all_sentences()):
    print(f'Start sentence {i}')
    
    # Define hook to get intermediate values
    hidden_states = torch.zeros(len(sentence), 1, 512)
    def hook(m, i):
        hidden_states.copy_(i[0].data)
                                
    h = ner.linear.register_forward_pre_hook(hook)
                                
    ner.predict(sentence)
                                
    spans = sentence.get_spans('ner')
                                
    # Informaction to store: the named entities, their predicted labels, probabilities and hidden states
    # If there are multiple words for one entity, take the average value of hidden states
    # and record the number of words in the entity
    
    for span in spans:
        entry = {}
        entry['text'] = span.text
        entry['tag'] = span.tag
        entry['score'] = span.score
        entry['token_num'] = len(span.tokens)
        
        idx = [token.idx-1 for token in span.tokens]
        entry['linear_layer_state'] = hidden_states[idx, :, :].mean(dim=0).squeeze().tolist()
        
        db_col.insert_one(entry)
    
    h.remove()
    
    print(f'Finish sentence {i}')

# Extract hidden states from pretrained en-sentiment model

In [3]:
train_pos = os.listdir('data/aclImdb_v1/aclImdb/train/pos/')
train_neg = os.listdir('data/aclImdb_v1/aclImdb/train/neg/')
test_pos = os.listdir('data/aclImdb_v1/aclImdb/test/pos/')
test_neg = os.listdir('data/aclImdb_v1/aclImdb/test/neg/')

In [5]:
pos_data = []
for name in train_pos:
    with open('data/aclImdb_v1/aclImdb/train/pos/' + name, 'r') as f:
        pos_data.append(f.readline())
for name in test_pos:
    with open('data/aclImdb_v1/aclImdb/test/pos/' + name, 'r') as f:
        pos_data.append(f.readline())

In [6]:
neg_data = []
for name in train_neg:
    with open('data/aclImdb_v1/aclImdb/train/neg/' + name, 'r') as f:
        neg_data.append(f.readline())
for name in test_neg:
    with open('data/aclImdb_v1/aclImdb/test/neg/' + name, 'r') as f:
        neg_data.append(f.readline())

### Load model

In [ ]:
import torch

In [4]:
sent_model = TextClassifier.load('en-sentiment')

In [11]:
# Set batch size
batch_size = 64

In [12]:
# Define hook to get intermediate values
records = torch.zeros(batch_size, 2048)

def hook(m, i, o):
    print(i[0].data.shape)
    records.copy_(i[0].data)

In [ ]:
# Add the hook to model
h = sent_model.decoder.register_forward_hook(hook)

In [9]:
len(pos_data) / batch_size

390.625

In [ ]:
for i in range(len(neg_data) // batch_size):
    sentences = [Sentence(s) for s in neg_data[batch_size * i: batch_size * (i+1)]]
    sent_model.predict(sentences, mini_batch_size=batch_size)
    labels = [sen.labels[0].to_dict() for sen in sentences]
    
    val_list = records.tolist()
    
    db_entries = [{
        'sentence': neg_data[batch_size * i + ix],
        'reduce_mean': val_list[ix],
        'label': labels[ix]
    } for ix in range(len(sentences))]
    
    val_collection.insert_many(db_entries)

# Database util

### Flattened val_collection

In [20]:
for rec in val_collection.find():
    break

In [10]:
rec['label']

{'value': 'POSITIVE', 'confidence': 1.0}

In [22]:
add_fields = [
    {'$addFields': {'sentiment': '$label.value', 'confidence': '$label.confidence'}},
    {'$out': 'flattened'}
]

In [24]:
flattened = db['flattened']

In [27]:
# delete label fields in the document store
flattened.update_many({}, {'$unset': {'label': ''}})

### Add index to val_collection

In [12]:
import pymongo

In [21]:
val_collection.create_index([('sentence', pymongo.TEXT)])

'sentence_text'

In [40]:
val_collection.create_index([('confidence', 1)])

'confidence_1'

In [46]:
val_collection.create_index('sentiment')

'sentiment_1'

In [61]:
# Test search on the index
cur = val_collection.find({
    '$and': [
        {'$text': {'$search': 'happy'}}, 
        {'sentiment': 'NEGATIVE'},
        {'confidence': {'$eq': 1.0}}
    ]
})

In [60]:
len(list(cur))

404

### Play with database

In [3]:
def query(term):
    pipeline = {
        '$text': {'$search': term}
    }

    return list(val_collection.find(pipeline))

In [8]:
res = query('\"movie\""')

In [84]:
vectors = np.array([elm['val'] for elm in res])

In [98]:
mean = np.mean(vectors, axis=0)
std = np.mean(vectors, axis=0)
stats = [
    {
        'dim': i,
        'mean': val[0],
        'std': val[1]
    } for i, val in enumerate(zip(mean, std))
]

### Utilities

In [127]:
pipeline = [
    {"$group": {"_id": "$sentence", "count": {"$sum": 1}}},
    {"$match": {"count": {"$gt": 1 }}}
]

In [128]:
res = val_collection.aggregate(pipeline, allowDiskUse=True)